### 🧠 Final Model Summary – Predicting Full Type Combinations

We extended our original classification task to predict a Pokémon’s **full typing combination** (e.g. `Water/Flying`, `Fire/`) as a single multiclass label, combining both **primary** and **secondary** types.

---

#### 📁 Dataset Overview

- **Kaggle Pokemon Database**: https://www.kaggle.com/datasets/mrdew25/pokemon-database  
- **Total Pokémon used**: `1,382` including alternate forms, or `1,054` base forms only
- **Target variable**: `type_combo` (combined primary and secondary type)  
  - Multiclass with **113 unique combinations** (after filtering low-frequency classes)

---

#### 🧪 Features Used
- Total: `858` after preprocessing 
- Raw stats: `Health`, `Attack`, `Defense`, `Sp. Attack`, `Sp. Defense`, `Speed`
- Composite stat: `Base Stat Total`
- Normalized stats (each stat as a % of total): `(Base Stat / Base Stat Total) * 100`
- Categorical traits: `Primary/Secondary Egg Groups`, `Primary Ability`, `Classification`
- Boolean flag: `is_pre_evolution` (whether the Pokémon has a pre-evo)

---

#### ✅ Model Comparison
| Model | Kappa Score | Notes |
|-------|-------------|-------|
| `MLPClassifier` | **0.570** | Performed well on most combos; improved with alternate forms |
| `RandomForest`  | **0.542** | Slightly worse; gets worse with alternate forms  |

---

#### 🔍 Key Observations
- Including **alternate forms** helped MLP significantly (similar to single-type task)
- For both models, **type prediction becomes harder** when combining primary + secondary into one target
- **Abilities** remained top features for MLP, while RF leaned on **stat-based signals**

---

#### 🎯 Summary
- Predicting full typing is a harder multiclass task than single-type prediction (go figure)
- MLP still leads, though the gap between RF and MLP narrowed in this setup
- Alternate forms provide valuable signal and improve performance consistency


In [29]:
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import OneHotEncoder, LabelEncoder
from sklearn.compose import ColumnTransformer
from sklearn.pipeline import Pipeline
from sklearn.neural_network import MLPClassifier
from sklearn.metrics import classification_report, cohen_kappa_score, confusion_matrix, ConfusionMatrixDisplay
import matplotlib.pyplot as plt
import numpy as np

# Load and clean data
df = pd.read_csv("../../data/pokemon_database.csv")
df = df.applymap(lambda x: x.strip('"') if isinstance(x, str) else x)
# df = df[df['Alternate Form Name'].isnull()]
df['Classification'] = df['Classification'].str.replace("(?i)\\s*pokemon\\s*", "", regex=True).str.strip()

# Create type combo
df['type_combo'] = df['Primary Type'] + '/' + df['Secondary Type'].fillna("")

# Feature setup
features = [
    'Primary Ability', 'Primary Egg Group', 'Secondary Egg Group', 'Classification',
    'Health Stat', 'Attack Stat', 'Defense Stat',
    'Special Attack Stat', 'Special Defense Stat', 'Speed Stat',
    'Base Stat Total'
]
df['is_pre_evolution'] = df['Pokemon Id'].isin(df['Pre-Evolution Pokemon Id'].dropna().astype(int))
features.append('is_pre_evolution')

# Normalize stats
for stat in ['Health Stat', 'Attack Stat', 'Defense Stat',
             'Special Attack Stat', 'Special Defense Stat', 'Speed Stat']:
    pct_feature = f"{stat}_pct"
    df[pct_feature] = (df[stat] / df['Base Stat Total']) * 100
    features.append(pct_feature)

# Initial modeling frame
df_model = df[features + ['type_combo']].dropna(subset=['type_combo'])

# Drop low-frequency type combos
combo_counts = df_model['type_combo'].value_counts()
valid_combos = combo_counts[combo_counts >= 2].index
df_model = df_model[df_model['type_combo'].isin(valid_combos)].copy()

# Recreate label encoder AFTER filtering
X = df_model[features]
y = df_model['type_combo']
label_encoder = LabelEncoder()
y_encoded = label_encoder.fit_transform(y)
df_model['type_combo_encoded'] = y_encoded  # For indexed access later

categorical_features = ['Primary Ability', 'Primary Egg Group', 'Secondary Egg Group', 'Classification']
numeric_features = [col for col in X.columns if col not in categorical_features]

# Preprocessor and model
preprocessor = ColumnTransformer(transformers=[
    ('cat', OneHotEncoder(handle_unknown='ignore'), categorical_features),
    ('num', 'passthrough', numeric_features)
])

model = Pipeline([
    ('preprocessor', preprocessor),
    ('classifier', MLPClassifier(hidden_layer_sizes=(256, 128), max_iter=500, learning_rate_init=0.001, random_state=42))
])

# Split and train
X_train, X_test, y_train, y_test = train_test_split(
    X, y_encoded, stratify=y_encoded, test_size=0.2, random_state=42
)

model.fit(X_train, y_train)
y_pred = model.predict(X_test)

# Evaluation
print("Unique type combinations:", len(label_encoder.classes_))
print("Test set size:", len(y_test))
print("Classification Report:\n")
print(classification_report(
    y_test, y_pred,
    labels=np.unique(y_test),
    target_names=label_encoder.inverse_transform(np.unique(y_test))
))

kappa = cohen_kappa_score(y_test, y_pred)
print(f"Cohen's Kappa Score: {kappa:.3f}")

# Confusion Matrix
labels = range(len(label_encoder.classes_))
cm = confusion_matrix(y_test, y_pred, labels=labels, normalize='true')
fig, ax = plt.subplots(figsize=(80, 80))  # 👈 Bigger plot for 100+ classes
disp = ConfusionMatrixDisplay(confusion_matrix=cm, display_labels=label_encoder.classes_)
disp.plot(ax=ax, xticks_rotation=90, cmap='Blues')  # Rotated labels for space
# Bigger font for tick labels
ax.set_xticklabels(ax.get_xticklabels(), fontsize=30)
ax.set_yticklabels(ax.get_yticklabels(), fontsize=30)

# Title and layout
plt.title("Normalized Confusion Matrix – Type Combos (Large Format)", fontsize=36)
plt.grid(False)
plt.tight_layout()
plt.show()


/var/folders/ht/dp3tdfgs34g1r1j0jdjb1qq40000gn/T/ipykernel_28764/4116125279.py:13: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df = df.applymap(lambda x: x.strip('"') if isinstance(x, str) else x)


Unique type combinations: 174
Test set size: 267
Classification Report:

                  precision    recall  f1-score   support

            Bug/       0.33      0.60      0.43         5
    Bug/Electric       1.00      1.00      1.00         1
    Bug/Fighting       0.00      0.00      0.00         1
      Bug/Flying       1.00      0.86      0.92         7
       Bug/Grass       0.00      0.00      0.00         1
      Bug/Poison       0.33      0.50      0.40         2
     Bug/Psychic       1.00      1.00      1.00         1
        Bug/Rock       0.00      0.00      0.00         1
       Bug/Steel       0.00      0.00      0.00         1
       Bug/Water       0.00      0.00      0.00         1
           Dark/       0.40      0.67      0.50         3
     Dark/Dragon       1.00      1.00      1.00         1
      Dark/Fairy       1.00      1.00      1.00         1
       Dark/Fire       0.50      1.00      0.67         1
     Dark/Flying       0.00      0.00      0.00         

/Users/rohanhangal/PersonalProjects/data_engineering/pokemon_project/venv/lib/python3.13/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/Users/rohanhangal/PersonalProjects/data_engineering/pokemon_project/venv/lib/python3.13/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/Users/rohanhangal/PersonalProjects/data_engineering/pokemon_project/venv/lib/python3.13/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicte

#### ✅ Model - RF

In [31]:
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import OneHotEncoder, LabelEncoder
from sklearn.compose import ColumnTransformer
from sklearn.pipeline import Pipeline
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import classification_report, cohen_kappa_score, confusion_matrix, ConfusionMatrixDisplay
import matplotlib.pyplot as plt
import numpy as np

# Load and clean data
df = pd.read_csv("../../data/pokemon_database.csv")
df = df.applymap(lambda x: x.strip('"') if isinstance(x, str) else x)
df = df[df['Alternate Form Name'].isnull()]
df['Classification'] = df['Classification'].str.replace("(?i)\\s*pokemon\\s*", "", regex=True).str.strip()

# Create type combo
df['type_combo'] = df['Primary Type'] + '/' + df['Secondary Type'].fillna("")


# Feature setup
features = [
    'Primary Ability', 'Primary Egg Group', 'Secondary Egg Group', 'Classification',
    'Health Stat', 'Attack Stat', 'Defense Stat',
    'Special Attack Stat', 'Special Defense Stat', 'Speed Stat',
    'Base Stat Total'
]
df['is_pre_evolution'] = df['Pokemon Id'].isin(df['Pre-Evolution Pokemon Id'].dropna().astype(int))
features.append('is_pre_evolution')

# Normalize stats
for stat in ['Health Stat', 'Attack Stat', 'Defense Stat',
             'Special Attack Stat', 'Special Defense Stat', 'Speed Stat']:
    pct_feature = f"{stat}_pct"
    df[pct_feature] = (df[stat] / df['Base Stat Total']) * 100
    features.append(pct_feature)

# Filter usable data
df_model = df[features + ['type_combo']].dropna(subset=['type_combo'])
combo_counts = df_model['type_combo'].value_counts()
valid_combos = combo_counts[combo_counts >= 2].index
df_model = df_model[df_model['type_combo'].isin(valid_combos)].copy()

# Encode
X = df_model[features]
y = df_model['type_combo']
label_encoder = LabelEncoder()
y_encoded = label_encoder.fit_transform(y)

categorical_features = ['Primary Ability', 'Primary Egg Group', 'Secondary Egg Group', 'Classification']
numeric_features = [col for col in X.columns if col not in categorical_features]

preprocessor = ColumnTransformer(transformers=[
    ('cat', OneHotEncoder(handle_unknown='ignore'), categorical_features),
    ('num', 'passthrough', numeric_features)
])

model = Pipeline([
    ('preprocessor', preprocessor),
    ('classifier', RandomForestClassifier(n_estimators=300, max_depth=30, random_state=42))
])

# Train/test split
X_train, X_test, y_train, y_test = train_test_split(
    X, y_encoded, stratify=y_encoded, test_size=0.2, random_state=42
)

# Fit + Predict
model.fit(X_train, y_train)
y_pred = model.predict(X_test)

# Eval
print("Unique type combinations:", len(label_encoder.classes_))
print("Test set size:", len(y_test))
print(classification_report(
    y_test, y_pred,
    labels=np.unique(y_test),
    target_names=label_encoder.inverse_transform(np.unique(y_test))
))
print("Kappa (RF):", cohen_kappa_score(y_test, y_pred))


# Confusion Matrix
labels = range(len(label_encoder.classes_))
cm = confusion_matrix(y_test, y_pred, labels=labels, normalize='true')
fig, ax = plt.subplots(figsize=(80, 80))  # 👈 Bigger plot for 100+ classes
disp = ConfusionMatrixDisplay(confusion_matrix=cm, display_labels=label_encoder.classes_)
disp.plot(ax=ax, xticks_rotation=90, cmap='Blues')  # Rotated labels for space
# Bigger font for tick labels
ax.set_xticklabels(ax.get_xticklabels(), fontsize=30)
ax.set_yticklabels(ax.get_yticklabels(), fontsize=30)

# Title and layout
plt.title("Normalized Confusion Matrix – Type Combos (Large Format)", fontsize=36)
plt.grid(False)
plt.tight_layout()
plt.show()


/var/folders/ht/dp3tdfgs34g1r1j0jdjb1qq40000gn/T/ipykernel_28764/443486346.py:13: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df = df.applymap(lambda x: x.strip('"') if isinstance(x, str) else x)


Unique type combinations: 149
Test set size: 200
                 precision    recall  f1-score   support

           Bug/       0.30      0.60      0.40         5
   Bug/Electric       1.00      1.00      1.00         1
   Bug/Fighting       0.00      0.00      0.00         1
     Bug/Flying       0.75      1.00      0.86         3
      Bug/Grass       0.00      0.00      0.00         1
     Bug/Poison       1.00      0.50      0.67         2
    Bug/Psychic       0.00      0.00      0.00         1
       Bug/Rock       0.00      0.00      0.00         1
      Bug/Steel       0.00      0.00      0.00         1
      Bug/Water       0.00      0.00      0.00         1
          Dark/       0.00      0.00      0.00         3
    Dark/Dragon       0.00      0.00      0.00         1
     Dark/Fairy       1.00      1.00      1.00         1
      Dark/Fire       0.00      0.00      0.00         1
    Dark/Flying       0.00      0.00      0.00         1
       Dark/Ice       0.00      0.00  

/Users/rohanhangal/PersonalProjects/data_engineering/pokemon_project/venv/lib/python3.13/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/Users/rohanhangal/PersonalProjects/data_engineering/pokemon_project/venv/lib/python3.13/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/Users/rohanhangal/PersonalProjects/data_engineering/pokemon_project/venv/lib/python3.13/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicte